# Part2 機械学習の進め方 Chap.6 モデルチューニング

## 6.1 LightGBMのハイパーパラメータのチューニング

- <https://lightgbm.readthedocs.io/en/latest/Parameters.html>
- 手動チューニング
- 自動チューニング

### 6.1.1 ハイパーパラメータの手動チューニング

- 対象とするモデルの仕組みの理解
  - 決定木
  - 勾配ブースティング
- モデルの仕組みとハイパーパラメータの関係
  - 勾配ブースティングの構成に関するもの
  - 決定木の構成に関するもの
  - 過学習の抑制に関するもの

### 6.1.2 ハイパーパラメータの自動チューニング

- 「値のパターン」を指定して探索するアプローチ
  - 事前に項目ごとにパターンを設定して、その組合せの範囲内で探索する
    - グリッドリサーチ
    - ランダムサーチ
- 「値の範囲」を指定して探索するアプローチ
  - 範囲だけを指定して、その中で最適な値を探索する

#### optunaを用いたハイパーパラメータの自動チューニングの例

In [5]:
# ライブラリの読み込み
import numpy as np
import pandas as pd
import os
import pickle
import gc

# オリジナルで追加
from pprint import pprint
from IPython.display import display

# 分布確認
# import pandas_profiling as pdp
# 可視化
import matplotlib.pyplot as plt

# 前処理
from sklearn.preprocessing import StandardScaler, MinMaxScaler, LabelEncoder, OneHotEncoder

# モデリング
from sklearn.model_selection import train_test_split, KFold, StratifiedKFold
from sklearn.metrics import accuracy_score, roc_auc_score, confusion_matrix
import lightgbm as lgb
import optuna

import warnings
warnings.filterwarnings("ignore")


In [2]:
# ファイルの読み込み
df_train = pd.read_csv("./titanic/train.csv")
display(df_train.head())

PassengerId  Survived  Pclass  \
0            1         0       3   
1            2         1       1   
2            3         1       3   
3            4         1       1   
4            5         0       3   

                                                Name     Sex   Age  SibSp  \
0                            Braund, Mr. Owen Harris    male  22.0      1   
1  Cumings, Mrs. John Bradley (Florence Briggs Th...  female  38.0      1   
2                             Heikkinen, Miss. Laina  female  26.0      0   
3       Futrelle, Mrs. Jacques Heath (Lily May Peel)  female  35.0      1   
4                           Allen, Mr. William Henry    male  35.0      0   

   Parch            Ticket     Fare Cabin Embarked  
0      0         A/5 21171   7.2500   NaN        S  
1      0          PC 17599  71.2833   C85        C  
2      0  STON/O2. 3101282   7.9250   NaN        S  
3      0            113803  53.1000  C123        S  
4      0            373450   8.0500   NaN        S

In [3]:
# データセットの作成
x_train, y_train, id_train = df_train[["Pclass", "Fare"]], df_train[["Survived"]], df_train[["PassengerId"]]
print(x_train.shape, y_train.shape, id_train.shape)

(891, 2) (891, 1) (891, 1)


In [9]:
# 目的関数の定義

# 探索しないハイパーパラメータ
params_base = {
    "boosting_type": "gbdt",
    "objective": "binary",
    "metric": "auc",
    "learning_rate": 0.02,
    "n_estimators": 100000,
    "bagging_freq": 1,
    "seed": 123,
    "early_stopping_rounds": 100,
    "verbose": 10,
}

def objective(trial):
    # 探索するハイパーパラメータ
    params_tuning = {
        "num_leaves": trial.suggest_int("num_leaves", 8, 256),
        "min_data_in_leaf": trial.suggest_int("min_data_in_leaf", 5, 200),
        "min_sum_hessian_in_leaf": trial.suggest_float("min_sum_hessian_in_leaf", 1e-5, 1e-2, log=True),
        "feature_fraction": trial.suggest_float("feature_fraction", 0.5, 1.0),
        "bagging_fraction": trial.suggest_float("bagging_fraction", 0.5, 1.0),
        "lambda_l1": trial.suggest_float("lambda_l1", 1e-2, 1e2, log=True),
        "lambda_l2": trial.suggest_float("lambda_l2", 1e-2, 1e2, log=True),
    }
    params_tuning.update(params_base)

    # モデル学習・評価
    list_metrics = list()
    cv = list(StratifiedKFold(n_splits=5, shuffle=True, random_state=123).split(x_train, y_train ))
    for nfold in np.arange(5):
        idx_tr = cv[nfold][0]
        idx_va = cv[nfold][1]
        x_tr = x_train.loc[idx_tr, :]
        y_tr = y_train.loc[idx_tr, :]
        x_va = x_train.loc[idx_va, :]
        y_va = y_train.loc[idx_va, :]
        model = lgb.LGBMClassifier(**params_tuning)
        model.fit(
            x_tr,
            y_tr,
            eval_set=[(x_tr, y_tr), (x_va, y_va)]
        )
        y_va_pred = model.predict_proba(x_va)[:, 1]
        metric_va = accuracy_score(y_va, np.where(y_va_pred>=0.5, 1, 0))
        list_metrics.append(metric_va)

    # 評価値の計算
    metrics = np.mean(list_metrics)

    return metrics

In [10]:
# 最適化処理（探索の実行）
sampler = optuna.samplers.TPESampler(seed=123)
study = optuna.create_study(sampler=sampler)
study.optimize(objective, n_trials=30)
# 10s

[I 2024-03-01 20:29:09,098] A new study created in memory with name: no-name-7e7f5ac5-2295-4a10-b47d-5d9c54cffcb3


[LightGBM] [Warning] early_stopping_round is set=100, early_stopping_rounds=100 will be ignored. Current value: early_stopping_round=100
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=4.792414358623587e-05, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=4.792414358623587e-05
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l1 is set=0.492522233779106, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.492522233779106
[LightGBM] [Warning] lambda_l2 is set=83.76388146302445, reg_lambda=0.0 will be ignored. Current value: lambda_l2=83.76388146302445
[LightGBM] [Warning] feature_fraction is set=0.7756573845414456, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7756573845414456
[LightGBM] [Warning] bagging_fraction is set=0.8597344848927815, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8597344848927815
[LightGBM] [War

[I 2024-03-01 20:29:09,738] Trial 0 finished with value: 0.664478061640826 and parameters: {'num_leaves': 181, 'min_data_in_leaf': 61, 'min_sum_hessian_in_leaf': 4.792414358623587e-05, 'feature_fraction': 0.7756573845414456, 'bagging_fraction': 0.8597344848927815, 'lambda_l1': 0.492522233779106, 'lambda_l2': 83.76388146302445}. Best is trial 0 with value: 0.664478061640826.


[LightGBM] [Debug] Re-bagging, using 594 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 4 and depth = 3
[LightGBM] [Debug] Re-bagging, using 602 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 7 and depth = 5
[LightGBM] [Debug] Re-bagging, using 603 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 6 and depth = 4
[LightGBM] [Debug] Re-bagging, using 634 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 6 and depth = 4
Early stopping, best iteration is:
[599]	training's auc: 0.744285	valid_1's auc: 0.785866
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=4.792414358623587e-05, min_child_weight=0.001 will be ignored. Current value: min_

[I 2024-03-01 20:29:10,058] Trial 1 finished with value: 0.6712196346745339 and parameters: {'num_leaves': 178, 'min_data_in_leaf': 99, 'min_sum_hessian_in_leaf': 0.00015009027543233888, 'feature_fraction': 0.6715890080754348, 'bagging_fraction': 0.8645248536920208, 'lambda_l1': 0.567922374174008, 'lambda_l2': 0.01732652966363563}. Best is trial 0 with value: 0.664478061640826.


...

[LightGBM] [Warning] early_stopping_round is set=100, early_stopping_rounds=100 will be ignored. Current value: early_stopping_round=100
[LightGBM] [Warning] min_sum_hessian_in_leaf is set=0.001228372021029653, min_child_weight=0.001 will be ignored. Current value: min_sum_hessian_in_leaf=0.001228372021029653
[LightGBM] [Warning] bagging_freq is set=1, subsample_freq=0 will be ignored. Current value: bagging_freq=1
[LightGBM] [Warning] lambda_l1 is set=31.857275396545745, reg_alpha=0.0 will be ignored. Current value: lambda_l1=31.857275396545745
[LightGBM] [Warning] lambda_l2 is set=75.78455018273661, reg_lambda=0.0 will be ignored. Current value: lambda_l2=75.78455018273661
[LightGBM] [Warning] feature_fraction is set=0.5419623926769075, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.5419623926769075
[LightGBM] [Warning] bagging_fraction is set=0.9992038288867305, subsample=1.0 will be ignored. Current value: bagging_fraction=0.9992038288867305
[LightGBM] [War

[I 2024-03-01 20:29:17,707] Trial 28 finished with value: 0.6610445044253342 and parameters: {'num_leaves': 55, 'min_data_in_leaf': 44, 'min_sum_hessian_in_leaf': 8.746395073776509e-05, 'feature_fraction': 0.6583330313256339, 'bagging_fraction': 0.9570248608415114, 'lambda_l1': 3.8091663327550203, 'lambda_l2': 0.04902238263689492}. Best is trial 6 with value: 0.6161634548992531.


[LightGBM] [Debug] Re-bagging, using 686 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 6 and depth = 4
[LightGBM] [Debug] Re-bagging, using 687 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 3 and depth = 2
[LightGBM] [Debug] Re-bagging, using 680 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 6 and depth = 4
[LightGBM] [Debug] Re-bagging, using 674 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 3 and depth = 2
[LightGBM] [Debug] Re-bagging, using 693 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 6 and depth = 4
[LightGBM] [Debug] Re-bagging,

[I 2024-03-01 20:29:18,017] Trial 29 finished with value: 0.6161634548992531 and parameters: {'num_leaves': 135, 'min_data_in_leaf': 77, 'min_sum_hessian_in_leaf': 0.00040858882764479773, 'feature_fraction': 0.6159488988393838, 'bagging_fraction': 0.8650865470378836, 'lambda_l1': 25.14982308781062, 'lambda_l2': 0.26517734126234865}. Best is trial 6 with value: 0.6161634548992531.


[LightGBM] [Debug] Re-bagging, using 623 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and depth = 1
[LightGBM] [Debug] Re-bagging, using 607 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and depth = 1
[LightGBM] [Debug] Re-bagging, using 607 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 3 and depth = 2
[LightGBM] [Debug] Re-bagging, using 636 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and depth = 1
[LightGBM] [Debug] Re-bagging, using 617 data to train
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Debug] Trained a tree with leaves = 2 and depth = 1
[LightGBM] [Debug] Re-bagging,

In [12]:
# 探索結果の確認
trial = study.best_trial
print(f"acc(best) = {trial.value:.4f}")
display(trial.params)

acc(best) = 0.6162


{'num_leaves': 87,
 'min_data_in_leaf': 86,
 'min_sum_hessian_in_leaf': 0.003971252247766701,
 'feature_fraction': 0.6252276826982534,
 'bagging_fraction': 0.7415171321313522,
 'lambda_l1': 87.54657140659076,
 'lambda_l2': 1.1965765212602313}

In [13]:
# ベストなハイパーパラメータの取得
params_best = trial.params
params_best.update(params_base)
display(params_best)

{'num_leaves': 87,
 'min_data_in_leaf': 86,
 'min_sum_hessian_in_leaf': 0.003971252247766701,
 'feature_fraction': 0.6252276826982534,
 'bagging_fraction': 0.7415171321313522,
 'lambda_l1': 87.54657140659076,
 'lambda_l2': 1.1965765212602313,
 'boosting_type': 'gbdt',
 'objective': 'binary',
 'metric': 'auc',
 'learning_rate': 0.02,
 'n_estimators': 100000,
 'bagging_freq': 1,
 'seed': 123,
 'early_stopping_rounds': 100,
 'verbose': 10}

## 6.2 LightGBM以外のモデル利用

- scikit-learnの各種モデル
- ニューラルネットワーク

### 6.2.1 scikit-learnの各種モデル

- <https://scikit-learn.org/stable/index.html>

#### Titanicデータを用いた例: ロジスティック回帰

- 説明変数
  - Pclass
  - Age
  - Embarked

In [14]:
# ファイルの読み込みとデータセット作成
df_train = pd.read_csv("./titanic/train.csv")

x_train = df_train[["Pclass", "Age", "Embarked"]]
y_train = df_train[["Survived"]]

In [15]:
# 欠損値の補間
x_train["Age"] = x_train["Age"].fillna(x_train["Age"].mean())

x_train["Embarked"] = x_train["Embarked"].fillna(x_train["Embarked"].mode()[0])

In [16]:
# カテゴリ変数のの数値データへの変換
# one-hot-encoding
ohe = OneHotEncoder()
ohe.fit(x_train[["Embarked"]])
df_embarked = pd.DataFrame(
    ohe.transform(x_train[["Embarked"]]).toarray(),
    columns=["Embarked_{}".format(col) for col in ohe.categories_[0]]
)

x_train = pd.concat([x_train, df_embarked], axis=1)
x_train = x_train.drop(columns=["Embarked"])

In [17]:
# 数値データの正規化
x_train["Pclass"] = (x_train["Pclass"] - x_train["Pclass"].min()) / (x_train["Pclass"].max() - x_train["Pclass"].min())
x_train["Age"] = (x_train["Age"] - x_train["Age"].min()) / (x_train["Age"].max() - x_train["Age"].min())

In [18]:
# 学習データと検証データの分割（ホールドアウト検証）
x_tr, x_va, y_tr, y_va = train_test_split(
    x_train,
    y_train,
    test_size=0.2,
    stratify=y_train,
    random_state=123
)
print(x_tr.shape, x_va.shape, y_tr.shape, y_va.shape)

(712, 5) (179, 5) (712, 1) (179, 1)


In [19]:
# LogisticRegression

# モデル定義
from sklearn.linear_model import LogisticRegression
model_logis = LogisticRegression()

# 学習
model_logis.fit(x_tr, y_tr)

# 予測
y_va_pred = model_logis.predict(x_va)
print(f"accuracy:  {accuracy_score(y_va, y_va_pred):.4f}")
print(y_va_pred[:5])

accuracy:  0.7263
[0 1 0 1 0]


In [20]:
# 確率値の取得
y_va_pred_proba = model_logis.predict_proba(x_va)
print(y_va_pred_proba[:5, :])
# [0の確率, 1の確率]

[[0.83618537 0.16381463]
 [0.23042987 0.76957013]
 [0.83241317 0.16758683]
 [0.32206475 0.67793525]
 [0.62565665 0.37434335]]


#### Titanicデータを用いた例: SVM

In [21]:
# SVM(Support Vector Machine)

# モデル定義
from sklearn.svm import SVC
model_svm = SVC(C=1.0, random_state=123, probability=True)

# 学習
model_svm.fit(x_tr, y_tr)

# 予測
y_va_pred = model_svm.predict(x_va)
print(f"accuracy:  {accuracy_score(y_va, y_va_pred):.4f}")
print(y_va_pred[:5])

# 確率値の取得
y_va_pred_proba = model_svm.predict_proba(x_va)
print(y_va_pred_proba[:5, :])
# [0の確率, 1の確率]

accuracy:  0.7151
[0 1 0 1 0]
[[0.73985924 0.26014076]
 [0.28242534 0.71757466]
 [0.73986177 0.26013823]
 [0.26828214 0.73171786]
 [0.58950192 0.41049808]]


### 6.2.2 ニューラルネットワーク

- 欠損値を埋めないと学習できない
- すべて数値データにしないと学習できない
- 数値を正規化あるいは標準化する


- テーブルデータにニューラルネットワークを適用する例
  - 全結合層
  - 埋め込み層

#### ニューラルネットワークの適用例: 1 全結合層のみのネットワークモデル

In [4]:
# tensorflowライブラリのインポート
# https://www.tensorflow.org/install/pip?hl=ja
# python 3.12.2 では、tensorflowは実行できない
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Input, Dense, Dropout, BatchNormalization
from tensorflow.keras.layers import Embedding, Flatten, Concatenate
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint, ReduceLROnPlateau, LearningRateScheduler
from tensorflow.keras.optimizers import Adam, SGD

ModuleNotFoundError: No module named 'distutils'

## 6.3 アンサンブル

- 単純平均
- 重み付き平均（weighted average）
- スタッキング（stacking）

### 6.3.1 単純平均

#### サンプルデータを用いたアンサンブル（単純平均）の例

In [10]:
# 3モデルの予測値を持つデータフレームを算数で作成
np.random.seed(123)
df = pd.DataFrame(
    {
        "true": [0]*700 + [1]*300,
        "pred1": np.arange(1000) + np.random.rand(1000)*1200,
        "pred2": np.arange(1000) + np.random.rand(1000)*1000,
        "pred3": np.arange(1000) + np.random.rand(1000)*800,
    }
)
df["pred1"] = np.clip(df["pred1"]/df["pred1"].max(), 0, 1)
df["pred2"] = np.clip(df["pred2"]/df["pred2"].max(), 0, 1)
df["pred3"] = np.clip(df["pred3"]/df["pred3"].max(), 0, 1)

df_train, df_test = train_test_split(df, test_size=0.8, stratify=df["true"], random_state=123)
df_train = df_train.reset_index(drop=True)
df_test = df_test.reset_index(drop=True)
df_train.head()

true     pred1     pred2     pred3
0     1  0.683821  0.874443  0.859939
1     0  0.540691  0.113419  0.197144
2     0  0.310541  0.334798  0.599304
3     0  0.043486  0.170622  0.378528
4     0  0.550847  0.354703  0.598860

In [11]:
# 単純平均によるアンサンブル
df_train["pred_ensemble1"] = (df_train["pred1"] + df_train["pred2"] + df_train["pred3"]) / 3
df_train.head()

true     pred1     pred2     pred3  pred_ensemble1
0     1  0.683821  0.874443  0.859939        0.806068
1     0  0.540691  0.113419  0.197144        0.283752
2     0  0.310541  0.334798  0.599304        0.414881
3     0  0.043486  0.170622  0.378528        0.197545
4     0  0.550847  0.354703  0.598860        0.501470

In [12]:
# アンサンブル用の精度評価関数
def evaluate_ensemble(input_df, col_pred):
    model1_auc = roc_auc_score(input_df["true"], input_df["pred1"])
    model2_auc = roc_auc_score(input_df["true"], input_df["pred2"])
    model3_auc = roc_auc_score(input_df["true"], input_df["pred3"])
    ensemble_auc = roc_auc_score(input_df["true"], input_df[col_pred])
    print(
        f"model1:  {model1_auc:.4f}, model2:  {model2_auc:.4f}, model3:  {model3_auc:.4f} -> ensemble:  {ensemble_auc:.4f}"
    )

In [13]:
# アンサンブルの精度評価
evaluate_ensemble(df_train, col_pred="pred_ensemble1")

model1:  0.8342, model2:  0.8671, model3:  0.9050 -> ensemble:  0.9585


In [14]:
# 推論時のアンサンブル処理と精度評価
df_test["pred_ensemble1"] = (df_test["pred1"] + df_test["pred2"] + df_test["pred3"]) / 3
evaluate_ensemble(df_test, col_pred="pred_ensemble1")

model1:  0.8086, model2:  0.8398, model3:  0.8973 -> ensemble:  0.9396


### 6.3.2 重み付き平均

#### サンプルデータを用いたアンサンブル（重み付き平均）の例

In [16]:
# 重み付き平均によるアンサンブル
weight = [0.3, 0.3, 0.4]
print(weight)
weight = weight / np.sum(weight)
print(weight)

df_train["pred_ensemble2"] = (
    df_train["pred1"] * weight[0] + df_train["pred2"] * weight[1] + df_train["pred3"] * weight[2]
)
df_train[["true", "pred1", "pred2", "pred3", "pred_ensemble2"]].head()

[0.3, 0.3, 0.4]
[0.3 0.3 0.4]


true     pred1     pred2     pred3  pred_ensemble2
0     1  0.683821  0.874443  0.859939        0.811455
1     0  0.540691  0.113419  0.197144        0.275091
2     0  0.310541  0.334798  0.599304        0.433324
3     0  0.043486  0.170622  0.378528        0.215643
4     0  0.550847  0.354703  0.598860        0.511209

In [17]:
# アンサンブルの精度評価
evaluate_ensemble(df_train, col_pred="pred_ensemble2")

model1:  0.8342, model2:  0.8671, model3:  0.9050 -> ensemble:  0.9614


In [18]:
# 推論時のアンサンブル処理と精度評価
df_test["pred_ensemble2"] = (
    df_test["pred1"] * weight[0] + df_test["pred2"] * weight[1] + df_test["pred3"] * weight[2]
)
evaluate_ensemble(df_test, col_pred="pred_ensemble2")

model1:  0.8086, model2:  0.8398, model3:  0.8973 -> ensemble:  0.9420


### 6.3.3 スタッキング

#### サンプルデータを用いたアンサンブル（スタッキング）の例

In [20]:
# スタッキングによるアンサンブル
from sklearn.linear_model import Lasso

x = df_train[["pred1", "pred2", "pred3"]]
y = df_train[["true"]]
oof = np.zeros(len(x))
models = list()

cv = list(StratifiedKFold(n_splits=5, shuffle=True, random_state=123).split(x, y))
for nfold in np.arange(5):
    # 学習データと検証データの分離
    idx_tr = cv[nfold][0]
    idx_va = cv[nfold][1]
    x_tr = x.loc[idx_tr, :]
    y_tr = y.loc[idx_tr, :]
    x_va = x.loc[idx_va, :]
    y_va = y.loc[idx_va, :]

    # モデル学習
    model = Lasso(alpha=0.01)
    model.fit(x_tr, y_tr)
    models.append(model)

    # 検証データの予測値算出
    y_va_pred = model.predict(x_va)
    oof[idx_va] = y_va_pred

df_train["pred_ensemble3"] = oof
df_train["pred_ensemble3"] = df_train["pred_ensemble3"].clip(lower=0, upper=1)
df_train[["true", "pred1", "pred2", "pred3", "pred_ensemble3"]].head()

true     pred1     pred2     pred3  pred_ensemble3
0     1  0.683821  0.874443  0.859939        0.745020
1     0  0.540691  0.113419  0.197144        0.000000
2     0  0.310541  0.334798  0.599304        0.206734
3     0  0.043486  0.170622  0.378528        0.000000
4     0  0.550847  0.354703  0.598860        0.303498

In [21]:
# アンサンブルの精度評価
evaluate_ensemble(df_train, col_pred="pred_ensemble3")

model1:  0.8342, model2:  0.8671, model3:  0.9050 -> ensemble:  0.9577


In [24]:
# 推論時のアンサンブル処理と精度評価
df_test["pred_ensemble3"] = 0
for model in models:
    df_test["pred_ensemble3"] = model.predict(df_test[["pred1", "pred2", "pred3"]]) / len(models)

df_test["pred_ensemble3"] = df_test["pred_ensemble3"].clip(lower=0, upper=1)
evaluate_ensemble(df_test, col_pred="pred_ensemble3")

model1:  0.8086, model2:  0.8398, model3:  0.8973 -> ensemble:  0.9427
